In [1]:
import solara
import bpy
from pathlib import Path
from IPython.display import Image, display

# Reactive variable to track rendering status
do_render = solara.reactive(False)

def render_image():
    # Configure Blender rendering settings
    bpy.context.scene.render.engine = 'BLENDER_WORKBENCH'
    bpy.context.scene.render.resolution_x = 500
    bpy.context.scene.render.resolution_y = 200

    # Render and save the image
    output_path = Path.cwd() / "render_output.png"
    bpy.ops.render.render()
    bpy.data.images["Render Result"].save_render(filepath=str(output_path))
    
    return output_path
render_image()


PosixPath('/Users/jan-hendrik/projects/bpy4.2.0-solara/pages/render_output.png')

In [2]:
@solara.component
def Page():

    def render():
        if do_render.value:
            return render_image()
   
    result = solara.use_thread(render, [do_render.value])
    if not do_render.value:
        solara.Button("Start Rendering", on_click=lambda: do_render.set(True))
    else:
        if result.state == solara.ResultState.RUNNING:
            solara.Info("Rendering in progress...")
            solara.ProgressLinear()
        elif result.state == solara.ResultState.ERROR:
            solara.Error(f"Rendering failed: {result.error}")
        elif result.state == solara.ResultState.FINISHED:
            with solara.Column():
                solara.Success("Rendering complete.")
                if result.value:
                    # Display the rendered image using the Solara component
                    solara.Image(result.value)

# Run the Page component
Page()

Cannot show ipywidgets in text